In [44]:
#https://www.machinelearningplus.com/nlp/topic-modeling-visualization-how-to-present-results-lda-models/
import json
import numpy as np, pandas as pd
import matplotlib.pyplot as plt
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
sw_nltk = stopwords.words('english')
from nltk.tokenize.treebank import TreebankWordDetokenizer
#nltk.download('punkt')
from nltk.stem import WordNetLemmatizer
#nltk.download('wordnet')

import re

from matplotlib import cm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import (RepeatedStratifiedKFold, cross_val_score, )
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
from tomotopy import HDPModel

from lda_classification.model import TomotopyLDAVectorizer
from lda_classification.preprocess.spacy_cleaner import SpacyCleaner



#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
workers = 4 #Numbers of workers throughout the project
use_umap = False #make this True if you want to use UMAP for your visualizations
min_df = 5 #Minimum number for document frequency in the corpus
rm_top = 5 #Remove top n frequent words

In [69]:
#lem for lemmatization, stem for stemmatizing
def preprocess(data, type="lem"):
    preprocessed_data = []
    for x in data:
        #Lowerize
        x = x.lower()
        #Eliminate special characters
        x = re.sub(r'\d+', '', x)
        x = re.sub(' +', ' ', x.translate ({ord(c): "" for c in "!@#$%^&*()[]{};:,./<>?\|`~-=_+"}).strip())
        
        #Eliminate stop words
        words = [word for word in x.split() if word not in sw_nltk] 
        x = " ".join(words)

        #Stemming / Lemmatizing
        words = word_tokenize(x)
        rootWords = []
        if type=='stem':
                ps = PorterStemmer()
                rootWords.append(ps.stem(w))
        else:
            for w in words:
                wordnet_lemmatizer = WordNetLemmatizer()
                rootWords.append(wordnet_lemmatizer.lemmatize(w))

        x = TreebankWordDetokenizer().detokenize(rootWords)

        preprocessed_data.append(x)
    return preprocessed_data
        
    #print(preprocessed_data)


#preprocess(['Hsf##123 14: . ; ,  45', 'Blu34%& 22', 'as fine as good', 'found, find, go, went', 'studies studying cries cry'])

In [85]:
# Opening JSON file
f_queries = open('Queries_Labeled.json',)
f_collection = open('collection.json')
 
# returns JSON object as
# a dictionary
data_queries = json.load(f_queries)
data_collection = json.load(f_collection)
 
# Iterating through the json
# list
#for i in data['documents']:
#    print(i)
 
queries = data_queries['documents']
collection = data_collection['TREC']['DOC']
#print(len(queries))
#print(len(collection))

# Closing file
f_queries.close()
f_collection.close()


prep_collection = []
for x in collection:
    prep_collection.append(x['text'])
    prep_collection = preprocess(prep_collection)

prep_queries = []
for x in queries:
    prep_queries.append(x['text'])
    prep_queries = preprocess(prep_queries)

#print(prep_queries)
#print(prep_collection)

In [81]:

# Parameters tuning using Grid Search
tokens_collection = np.array()
for x in prep_collection:
    tokens_collection.append(np.array(word_tokenize(x)))


#vectorizer = CountVectorizer(analyzer='word',       
#                             min_df=10,
# minimum reqd occurences of a word 
 #                            stop_words='english',             
# remove stop words
  #                           lowercase=True,                   
# convert all words to lowercase
 #                            token_pattern='[a-zA-Z0-9]{3,}',  
# num chars > 3
                             # max_features=50000,             
# max number of uniq words    )
#data_vectorized = vectorizer.fit_transform(data_lemmatized)




print(tokens_collection)
from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.manifold import TSNE
grid_params = {'n_components' : list(range(5,10))}
# LDA model
lda = LatentDirichletAllocation()
lda_model = GridSearchCV(lda,param_grid=grid_params)
lda_model.fit(tokens_collection)
# Estimators for LDA model
lda_model1 = lda_model.best_estimator_
print("Best LDA model's params" , lda_model.best_params_)
print("Best log likelihood Score for the LDA model",lda_model.best_score_)
print("LDA model Perplexity on train data", lda_model1.perplexity(tokens_collection))

[array(['digital', 'computers', 'in', 'universities', '(', 'part', 'i',
       ')', 'july', ',', '1960', 'reeves', ',', 'r.', 'f.', 'ca600702',
       'jb', 'march', '20', ',', '1978', '9:20', 'pm'], dtype='<U12'), array(['using', 'synthetic', 'images', 'to', 'register', 'real', 'images',
       'with', 'surface', 'models', 'a', 'number', 'of', 'image',
       'analysis', 'tasks', 'can', 'benefit', 'from', 'registration',
       'of', 'the', 'image', 'with', 'a', 'model', 'of', 'the', 'surface',
       'being', 'imaged', '.', 'automatic', 'navigation', 'using',
       'visible', 'light', 'or', 'radar', 'images', 'requires', 'exact',
       'alignment', 'of', 'such', 'images', 'with', 'digital', 'terrain',
       'models', '.', 'in', 'addition', ',', 'automatic',
       'classification', 'of', 'terrain', ',', 'using', 'satellite',
       'imagery', ',', 'requires', 'such', 'alignment', 'to', 'deal',
       'correctly', 'with', 'the', 'effects', 'of', 'varying', 'sun',
       'angle', 'a

C:\Python38\lib\site-packages\numpy\core\_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)
C:\Python38\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Python38\lib\site-packages\sklearn\model_selection\_validation.py", line 529, in _fit_and_score
    estimator.fit(X_train, **fit_params)
  File "C:\Python38\lib\site-packages\sklearn\decomposition\_lda.py", line 556, in fit
    X = self._check_non_neg_array(X, reset_n_features=True,
  File "C:\Python38\lib\site-packages\sklearn\decomposition\_lda.py", line 482, in _check_non_

ValueError: Expected 2D array, got 1D array instead:
array=[array(['digital', 'computers', 'in', 'universities', '(', 'part', 'i',
       ')', 'july', ',', '1960', 'reeves', ',', 'r.', 'f.', 'ca600702',
       'jb', 'march', '20', ',', '1978', '9:20', 'pm'], dtype='<U12')
 array(['using', 'synthetic', 'images', 'to', 'register', 'real', 'images',
       'with', 'surface', 'models', 'a', 'number', 'of', 'image',
       'analysis', 'tasks', 'can', 'benefit', 'from', 'registration',
       'of', 'the', 'image', 'with', 'a', 'model', 'of', 'the', 'surface',
       'being', 'imaged', '.', 'automatic', 'navigation', 'using',
       'visible', 'light', 'or', 'radar', 'images', 'requires', 'exact',
       'alignment', 'of', 'such', 'images', 'with', 'digital', 'terrain',
       'models', '.', 'in', 'addition', ',', 'automatic',
       'classification', 'of', 'terrain', ',', 'using', 'satellite',
       'imagery', ',', 'requires', 'such', 'alignment', 'to', 'deal',
       'correctly', 'with', '